# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model
(Recurrent PPO) [default: 25 EVs per week simulation]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 399, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 399 (delta 0), reused 2 (delta 0), pack-reused 393
Receiving objects: 100% (399/399), 151.25 MiB | 22.35 MiB/s, done.
Resolving deltas: 100% (149/149), done.
Checking out files: 100% (108/108), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f049bc70ad0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 25
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 25, 'EVs_n_max': 1305, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27222.13 , over-consume=kWh  43837.21 , under-consume=kWh  16615.08 , Total_cost=€  1077.51 , overcost=€  1557.63 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

In [12]:
env.plot_VPP_supply_demand()

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  26523.99 , over-consume=kWh  43195.04 , under-consume=kWh  16671.05 , Total_cost=€  1061.18 , overcost=€  1537.82 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2620.42 , over-consume=KWh  1739.51 , under-consume=KWh  4359.94 , Total_cost=€  -50.69 , Overcost=€  60.71 
 EV_INFO: Av.EV_energy_leaving=kWh  64.8 , Std.EV_energy_leaving=kWh  24.42 , EV_departures =  1298 , EV_queue_left =  6
SCORE:  Cumulative_reward= 443379.96 - Step_rewars (load_t= 401347.89, EVs_energy_t= 12004.76)
 - Final_rewards (EVs_energy= 19509.54, Overconsume= -827.39, Underconsume= -1153.64, Overcost= 12498.8)
Episode:1 Score:443379.96151125804


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  50.618000  43.332790  52.727886  51.824928   
2022-01-01 00:15:00  50.868000  42.800598  52.195694  52.074928   
2022-01-01 00:30:00  51.118000  42.328896  51.723991  52.324928   
2022-01-01 00:45:00  51.368000  41.890896  51.285992  52.574928   
2022-01-01 01:00:00  51.618000  41.415455  50.810551  52.824928   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  88.201668  72.220871  27.870880  99.989998   
2022-06-06 05:00:00  89.965019  71.970871  27.620880  99.989998   
2022-06-06 05:15:00  91.678459  71.720871  27.370880  99.989998   
2022-06-06 05:30:00  93.501961  71.470871  27.120880  99.989998   
2022-06-06 05:45:00  95.173576  71.220871  26.870880  99.989998   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [3912, 3911, 3910, 3909]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [3912, 3911, 3910, 3909]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [3912, 3911, 3910, 3909]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [3912, 3911, 3910, 3909]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [4452, 4450, 4451, 4449]  [1, 2, 2, 1]   
2022-06-06 05:00:00  [4452, 4450, 4451, 4449]  [1, 2, 2, 1]   
2022-06-06 05:15:00  [4452, 4450, 4451, 4449]  [1, 2, 2, 1]   
2022-06-06 05:30:00  [4452, 4450, 4451, 4449]  [1, 2, 2, 1]   
2022-06-06 05:45:00  [4452, 4450, 4451, 4449]  [1, 2, 2, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00   [True, False, False, False]        5.451069   
2022-06-06 05:00:00   [True, False, False, False]        7.053407   
2022-06-06 05:15:00  [False, False, False, False]        6.853781   
2022-06-06 05:30:00  [False, False, False, False]        7.294000   
2022-06-06 05:45:00  [False, False, False, False]        6.686486   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  1.552722e+00    15.000000        0.0   
2022-01-01 00:15:00          -4.257543 -4.440892e-16    15.000000        0.0   
2022-01-01 00:30:00          -3.773612  0.000000e+00    15.000000        0.0   
2022-01-01 00:45:00          -3.503986 -2.220446e-16    15.000000        0.0   
2022-01-01 01:00:00          -3.803514 -2.220446e-16    15.000000        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -2.000000 -5.451052e+00    -7.775809        0.0   
2022-06-06 05:00:00          -2.000000 -7.053390e+00    -7.594331        0.0   
2022-06-06 05:15:00          -2.000000 -6.853764e+00    -7.994530        0.0   
2022-06-06 05:30:00          -2.000000 -7.293983e+00    -7.442245        0.0   
2022-06-06 05:45:00          -2.000000 -6.686469e+00    -8.127925        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00  -7.775809  
2022-06-06 05:00:00  -7.594331  
2022-06-06 05:15:00  -7.994530  
2022-06-06 05:30:00  -7.442245  
20

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

In [27]:
env.plot_VPP_supply_demand()

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5217, Arrival time: 2022-01-01 10:30:00, Parking_time: 24, Leaving_time: 2022-01-02 10:30:00, SOC: 0.49732384383086253, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6520, Arrival time: 2022-12-31 17:30:00, Parking_time: 23.50132353964689, Leaving_time: 2023-01-01 17:00:04.764743, SOC: 0.4040519014304283, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  17540.44 , over-consume=kWh  38111.41 , under-consume=kWh  20570.97 , Total_cost=€  860.2 , overcost=€  1684.72 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  74.71


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  17967.45 , over-consume=kWh  38985.13 , under-consume=kWh  21017.68 , Total_cost=€  848.35 , overcost=€  1701.42 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  74.71
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4764.46 , over-consume=KWh  1100.03 , under-consume=KWh  5864.49 , Total_cost=€  -175.61 , Overcost=€  46.91 
 EV_INFO: Av.EV_energy_leaving=kWh  69.56 , Std.EV_energy_leaving=kWh  23.7 , EV_departures =  1299 , EV_queue_left =  1
SCORE:  Cumulative_reward= 458083.94 - Step_rewars (load_t= 392483.37, EVs_energy_t= 31000.09)
 - Final_rewards (EVs_energy= 21656.06, Overconsume= -335.38, Underconsume= -1481.75, Overcost= 14761.54)
Episode:1 Score:458083.93787020806


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000  41.933807   0.000000   0.000000   
2022-01-01 00:45:00   0.000000  42.847435   0.000000   0.000000   
2022-01-01 01:00:00   0.000000  43.773201   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  83.177017  51.399628  40.265579  93.760674   
2022-06-06 05:00:00  84.393166  51.149628  41.481728  94.976822   
2022-06-06 05:15:00  85.258217  52.014675  42.346775  95.841873   
2022-06-06 05:30:00  86.119667  52.876122  43.208221  96.703323   
2022-06-06 05:45:00  87.011024  53.767479  44.099579  97.594681   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00           [0, 7825, 0, 0]  [0, 1, 0, 2]   
2022-01-01 00:45:00           [0, 7825, 0, 0]  [0, 1, 2, 2]   
2022-01-01 01:00:00           [0, 7825, 0, 0]  [0, 1, 2, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [8348, 8346, 8347, 8345]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [8348, 8346, 8347, 8345]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [8348, 8346, 8347, 8345]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [8348, 8346, 8347, 8345]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [8348, 8346, 8347, 8345]  [1, 1, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00    [True, True, True, False]        0.000000   
2022-01-01 00:45:00   [True, True, False, False]        3.654511   
2022-01-01 01:00:00   [True, True, False, False]        3.703062   
...                                          ...             ...   
2022-06-06 04:45:00   [True, False, True, False]       11.281799   
2022-06-06 05:00:00    [True, True, True, False]       14.593785   
2022-06-06 05:15:00    [True, True, True, False]       13.840767   
2022-06-06 05:30:00    [True, True, True, False]       13.783149   
2022-06-06 05:45:00    [True, True, True, False]       14.261716   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.577770    -5.063691   0.000000   
2022-01-01 00:15:00                0.0 -4.070061    -4.481829   0.000000   
2022-01-01 00:30:00                0.0 -3.689098    15.000000   0.000000   
2022-01-01 00:45:00                0.0  0.000000    15.000000   0.000000   
2022-01-01 01:00:00                0.0  0.000000    15.000000   0.000000   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00               -1.0  0.000000    15.000000   0.000000   
2022-06-06 05:00:00               -1.0  0.000000    15.000000   0.000000   
2022-06-06 05:15:00                0.0  0.000000    15.000000   0.000000   
2022-06-06 05:30:00                0.0  0.000000    15.000000   0.000000   
2022-06-06 05:45:00                0.0  0.000000    15.000000  64.479746   

                       rewards  
time                            
2022-01-01 00:00:00  -5.063691  
2022-01-01 00:15:00  -4.481829  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:45:00  79.479746  

[15000 rows x 13 columns]

In [40]:
env.plot_VPP_results()


In [41]:
env.plot_VPP_supply_demand()

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 9129, Arrival time: 2022-01-01 08:45:00, Parking_time: 22.490279631586723, Leaving_time: 2022-01-02 07:14:25.006674, SOC: 0.7036401683466529, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 10432, Arrival time: 2022-12-31 21:15:00, Parking_time: 23.904373229928005, Leaving_time: 2023-01-01 21:09:15.743628, SOC: 0.39886199591210164, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14700.51 , over-consume=kWh  36907.26 , under-consume=kWh  22206.75 , Total_cost=€  709.62 , overcost=€  1535.59 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  77.36


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14715.02 , over-consume=kWh  36840.24 , under-consume=kWh  22125.23 , Total_cost=€  719.31 , overcost=€  1533.52 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  77.36
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -5535.33 , over-consume=KWh  860.87 , under-consume=KWh  6396.2 , Total_cost=€  -179.44 , Overcost=€  34.27 
 EV_INFO: Av.EV_energy_leaving=kWh  71.93 , Std.EV_energy_leaving=kWh  22.93 , EV_departures =  1299 , EV_queue_left =  1
SCORE:  Cumulative_reward= 465153.77 - Step_rewars (load_t= 387902.91, EVs_energy_t= 41239.03)
 - Final_rewards (EVs_energy= 22065.14, Overconsume= -137.45, Underconsume= -1670.45, Overcost= 15754.58)
Episode:1 Score:465153.76557182125


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0          1          2    3                EVs_id  \
time                                                                        
2022-01-01 00:00:00  0.0   0.000000   0.000000  0.0          [0, 0, 0, 0]   
2022-01-01 00:15:00  0.0   0.000000   0.000000  0.0          [0, 0, 0, 0]   
2022-01-01 00:30:00  0.0   0.000000   0.000000  0.0          [0, 0, 0, 0]   
2022-01-01 00:45:00  0.0   0.000000   0.000000  0.0          [0, 0, 0, 0]   
2022-01-01 01:00:00  0.0   0.000000   0.000000  0.0          [0, 0, 0, 0]   
...                  ...        ...        ...  ...                   ...   
2022-06-06 03:30:00  0.0  67.711655  70.570946  0.0  [0, 12285, 12286, 0]   
2022-06-06 03:45:00  0.0  67.711655  71.528503  0.0  [0, 12285, 12286, 0]   
2022-06-06 04:00:00  0.0  67.711655  73.212334  0.0  [0, 12285, 12286, 0]   
2022-06-06 04:15:00  0.0  67.711655  75.016121  0.0  [0, 12285, 12286, 0]   
2022-06-06 04:30:00  0.0  67.711655  76.519585  0.0  [0, 12285, 12286, 0]   

                          actions                   mask_truth  \
time                                                             
2022-01-01 00:00:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:15:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:30:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:45:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 01:00:00  [2, 0, 1, 0]   [False, True, False, True]   
...                           ...                          ...   
2022-06-06 03:30:00  [2, 0, 1, 2]  [False, False, True, False]   
2022-06-06 03:45:00  [2, 0, 1, 2]  [False, False, True, False]   
2022-06-06 04:00:00  [2, 0, 1, 2]  [False, False, True, False]   
2022-06-06 04:15:00  [2, 0, 1, 2]  [False, False, True, False]   
2022-06-06 04:30:00  [2, 0, 1, 2]  [False, False, True, False]   

                     ev_charged_pwr  ev_discharged_pwr      load  load_reward  \
time                                                                            
2022-01-01 00:00:00        0.000000                0.0 -2.562893    -4.192012   
2022-01-01 00:15:00        0.000000                0.0 -3.515207    -3.925354   
2022-01-01 00:30:00        0.000000                0.0 -3.355212    -3.989234   
2022-01-01 00:45:00        0.000000                0.0 -3.393540    -6.238596   
2022-01-01 01:00:00        0.000000                0.0 -5.362455    -6.319971   
...                             ...                ...       ...          ...   
2022-06-06 03:30:00        2.609291                0.0  0.000000    15.000000   
2022-06-06 03:45:00        3.830233                0.0  0.000000    15.000000   
2022-06-06 04:00:00        6.735306                0.0  0.000000    15.000000   
2022-06-06 04:15:00        7.215149                0.0  0.000000    15.000000   
2022-06-06 04:30:00        6.013858                0.0  0.000000    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.192012  
2022-01-01 00:15:00        0.0  -3.925354  
2022-01-01 00:30:00        0.0  -3.989234  
2022-01-01 00:45:00        0.0  -6.238596  
2022-01-01 01:00:00        0.0  -6.319971  
...                        ...        ...  
2022-06-06 03:30:00        0.0  15.000000  
2022-06-06 03:45:00        0.0  15.000000  
2022-06-06 04:00:00        0.0  15.000000  
2022-06-06 04:15:00        0.0  15.000000  
2022-06-06 04:30:00        0.0  15.000000  

[14995 rows x 13 columns]

In [54]:
env.plot_VPP_results()

In [55]:
env.plot_VPP_supply_demand()

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

In [63]:
#env.close()